# Method plots

## Setup notebook
Import our required packages and set default plotting options.

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
from tqdm import tqdm_notebook
from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML
from scipy import stats
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from matplotlib.ticker import MultipleLocator
from matplotlib.lines import Line2D
from cycler import cycler
from scipy.interpolate import interp1d
from pandas.api.types import CategoricalDtype
import seaborn as sns
sns.set(style="white")
from scipy import interpolate
from tqdm import tqdm

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10, 6)
plt.rcParams['axes.grid'] = True
plt.rcParams['grid.alpha'] = 0.3
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"
plt.rcParams['grid.linewidth'] = 0.5
plt.rcParams['axes.grid'] = True

# # https://stackoverflow.com/a/20709149
matplotlib.rcParams['text.usetex'] = True
matplotlib.rcParams['font.family'] = 'sans-serif'

# # matplotlib.rcParams['text.latex.preamble'] = [
# #        r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
# #        r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
# #        r'\usepackage{helvet}',    # set the normal font here
# #        r'\usepackage{amsmath}',
# #        r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
# #        r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
# # ]

matplotlib.rcParams['text.latex.preamble'] = [
    r'\usepackage{siunitx}',   # i need upright \micro symbols, but you need...
    r'\sisetup{detect-all}',   # ...this to force siunitx to actually use your fonts
    r'\usepackage[default]{sourcesanspro}',
    r'\usepackage{amsmath}',
       r'\usepackage{sansmath}',  # load up the sansmath so that math -> helvet
       r'\sansmath',              # <- tricky! -- gotta actually tell tex to use!
]

# import matplotlib as mpl
# mpl.use("pgf")
# pgf_with_custom_preamble = {
#     "font.family":"sans-serif",  # use serif/main font for text elements
#     "text.usetex":True,  # use inline math for ticks
#     "pgf.rcfonts":False,  # don't setup fonts from rc parameters
#     "pgf.preamble": [
#         r'\usepackage{siunitx}',  # i need upright \micro symbols, but you need...
#         r'\sisetup{detect-all}',  # ...this to force siunitx to actually use your fonts
#         r'\usepackage[default]{sourcesanspro}',
#         r'\usepackage{amsmath}',
#         r'\usepackage[mathrm=sym]{unicode-math}',
#         r'\setmathfont{Fira Math}',
#     ]
# }
# mpl.rcParams.update(pgf_with_custom_preamble)

## Import data
Import our data from the `./data/interim/` folder and load it into pandas dataframes. 

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_sites_waves = df_from_csv('sites_waves.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
    'postintertidal_slope_sto06': df_from_csv('impacts_forecasted_postintertidal_slope_sto06.csv', index_col=[0]),
    'postmean_slope_sto06': df_from_csv('impacts_forecasted_postmean_slope_sto06.csv', index_col=[0]),
    'preintertidal_slope_sto06': df_from_csv('impacts_forecasted_preintertidal_slope_sto06.csv', index_col=[0]),
    'premean_slope_sto06': df_from_csv('impacts_forecasted_premean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
    'postintertidal_slope_sto06': df_from_csv('twl_postintertidal_slope_sto06.csv', index_col=[0,1]),
    'postmean_slope_sto06': df_from_csv('twl_postmean_slope_sto06.csv', index_col=[0,1]),
    'preintertidal_slope_sto06': df_from_csv('twl_preintertidal_slope_sto06.csv', index_col=[0,1]),
    'premean_slope_sto06': df_from_csv('twl_premean_slope_sto06.csv', index_col=[0,1]),
    }
}
print('Done!')

# Plot example of swash and collision profiles

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(7, 2), dpi=300)
gs = gridspec.GridSpec(1, 3)
ax1 = fig.add_subplot(gs[0, 0])
ax2 = fig.add_subplot(gs[0, 1], sharey=ax1)
ax3 = fig.add_subplot(gs[0, 2], sharey=ax1)

prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'

plots = [
    {
        'ax': ax1,
        'title': 'Swash regime',
        'site_id': 'GRANTSn0009',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': '(a)',
        'xlim_left' : 50,
    },
    {
        'ax': ax2,
        'title': 'Collision regime',
        'site_id': 'MANNING0078',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': '(b)',
        'xlim_left' : 100,
    },
    {
        'ax': ax3,
        'title': 'Overwash regime',
        'site_id': 'AVOCAs0001',
        'x_min_fill': 80,
        'location': 'Avoca Lagoon\nEntrance',
        'subplot_letter': '(c)',
        'xlim_left' : 50,
    },
]

for plot in plots:
    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])
    df_feat_pre = df_profile_features_crest_toes.xs(
        (site_id, 'prestorm'), level=['site_id', 'profile_type'])
    df_feat_post = df_profile_features_crest_toes.xs(
        (site_id, 'poststorm'), level=['site_id', 'profile_type'])

    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--')
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color)
    ax.scatter(
        df_feat_post.dune_crest_x,
        df_feat_post.dune_crest_z,
        label='Poststorm dune crest',
        facecolor=poststorm_color,
        edgecolor='black',
        linewidth='0.75',
        marker='v',
        zorder=3)
    ax.scatter(
        df_feat_pre.dune_crest_x,
        df_feat_pre.dune_crest_z,
        label='Prestorm dune crest',
        facecolor=prestorm_color,
        edgecolor='black',
        linewidth='0.75',
        marker='v',
        zorder=3)

    if not np.isnan(df_feat_post.dune_toe_x.values[0]):
        ax.scatter(
            df_feat_post.dune_toe_x,
            df_feat_post.dune_toe_z,
            label='Poststorm dune toe',
            facecolor=poststorm_color,
            edgecolor='black',
            linewidth='0.75',
            marker='^',
            zorder=3)

    if not np.isnan(df_feat_pre.dune_toe_x.values[0]):
        ax.scatter(
            df_feat_pre.dune_toe_x,
            df_feat_pre.dune_toe_z,
            label='Prestorm dune toe',
            facecolor=prestorm_color,
            edgecolor='black',
            linewidth='0.75',
            marker='^',
            zorder=3)

    # Fill to zero elevation if there is no post profile value
    z_post = df_pro_post.z.values
    z_post[np.isnan(z_post)] = 0

    # Only want to fill the difference between pre/post past a certain x-val
    mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

    ax.fill_between(
        df_pro_post.index.get_level_values('x')[mask],
        df_pro_pre.z.values[mask],
        z_post[mask],
        color='#f46d43',
        label='Eroded volume',
        alpha=0.4)

    # Set lims
    ax.set_ylim([0, 10])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    
    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=7)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=8)

    # Add subplot letters
    ax.text(
        0.02,
        0.90,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=10,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

    # Add text showing location
    ax.text(
        0.95,
        0.95,
        plot['location'],
        transform=ax.transAxes,
        size=8,
        horizontalalignment='right',
        verticalalignment='top',
        zorder=3,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

# Remove tick parameters from shared axis
ax2.tick_params(labelleft=False)
ax3.tick_params(labelleft=False)

# Add y-label
ax1.set_ylabel('Elevation (mAHD)', size=8)

# Add common x-label
fig.text(
    0.5,
    -0.04,
    'Cross-shore position (m)',
    ha='center',
    size=8,
    horizontalalignment='center',
    verticalalignment='top')

# Add legend
ax1.legend(
    prop={'size': 6},
    ncol=4,
    bbox_to_anchor=(0.90, 1.0),
    loc="lower right",
    bbox_transform=fig.transFigure)

# Add title
fig.text(
0.06,1.01,
'Examples of observed\nstorm regimes',
horizontalalignment='left',
verticalalignment='bottom',
size=10)


fig.savefig('12_observed_storm_impacts.png',dpi=300, bbox_inches = "tight")
plt.show()

In [ ]:
## For coasts and ports

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(3, 1.2), dpi=300)
gs = gridspec.GridSpec(1, 3)
ax1 = fig.add_subplot(gs[0, 0])
ax2 = fig.add_subplot(gs[0, 1], sharey=ax1)
ax3 = fig.add_subplot(gs[0, 2], sharey=ax1)

prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'
scatter_marker_size=12
scatter_line_width = 0.6
plots = [
    {
        'ax': ax1,
        'title': 'Swash regime',
        'site_id': 'GRANTSn0009',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': '(a)',
        'xlim_left' : 50,
    },
    {
        'ax': ax2,
        'title': 'Collision regime',
        'site_id': 'MANNING0078',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': '(b)',
        'xlim_left' : 100,
    },
    {
        'ax': ax3,
        'title': 'Overwash regime',
        'site_id': 'AVOCAs0001',
        'x_min_fill': 80,
        'location': 'Avoca Lagoon\nEntrance',
        'subplot_letter': '(c)',
        'xlim_left' : 50,
    },
]

for plot in plots:
    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])
    df_feat_pre = df_profile_features_crest_toes.xs(
        (site_id, 'prestorm'), level=['site_id', 'profile_type'])
    df_feat_post = df_profile_features_crest_toes.xs(
        (site_id, 'poststorm'), level=['site_id', 'profile_type'])

    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--')
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color)
    ax.scatter(
        df_feat_post.dune_crest_x,
        df_feat_post.dune_crest_z,
        scatter_marker_size,
        label='Poststorm dune crest',
        facecolor=poststorm_color,
        edgecolor='black',
        linewidth=scatter_line_width,
        marker='v',
        zorder=3)
    ax.scatter(
        df_feat_pre.dune_crest_x,
        df_feat_pre.dune_crest_z,
        scatter_marker_size,
        label='Prestorm dune crest',
        facecolor=prestorm_color,
        edgecolor='black',
        linewidth=scatter_line_width,
        marker='v',
        zorder=3)

    if not np.isnan(df_feat_post.dune_toe_x.values[0]):
        ax.scatter(
            df_feat_post.dune_toe_x,
            df_feat_post.dune_toe_z,
            scatter_marker_size,
            label='Poststorm dune toe',
            facecolor=poststorm_color,
            edgecolor='black',
            linewidth=scatter_line_width,
            marker='^',
            zorder=3)

    if not np.isnan(df_feat_pre.dune_toe_x.values[0]):
        ax.scatter(
            df_feat_pre.dune_toe_x,
            df_feat_pre.dune_toe_z,
            scatter_marker_size,
            label='Prestorm dune toe',
            facecolor=prestorm_color,
            edgecolor='black',
            linewidth=scatter_line_width,
            marker='^',
            zorder=3)

    # Fill to zero elevation if there is no post profile value
    z_post = df_pro_post.z.values
    z_post[np.isnan(z_post)] = 0

    # Only want to fill the difference between pre/post past a certain x-val
    mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

    ax.fill_between(
        df_pro_post.index.get_level_values('x')[mask],
        df_pro_pre.z.values[mask],
        z_post[mask],
        color='#f46d43',
        label='Eroded volume',
        alpha=0.4)

    # Set lims
    ax.set_ylim([0, 10])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    
    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=6)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=6)

    # Add subplot letters
    ax.text(
        0.05,
        0.90,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=6,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

    # Add text showing location
    ax.text(
        0.95,
        0.95,
        plot['location'],
        transform=ax.transAxes,
        size=5,
        horizontalalignment='right',
        verticalalignment='top',
        zorder=3,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

# Remove tick parameters from shared axis
ax2.tick_params(labelleft=False)
ax3.tick_params(labelleft=False)

# Add y-label
ax1.set_ylabel('Elevation (mAHD)', size=8)

# Add common x-label
fig.text(
    0.5,
    -0.04,
    'Cross-shore position (m)',
    ha='center',
    size=8,
    horizontalalignment='center',
    verticalalignment='top')

plt.tight_layout(pad=0.1,w_pad=0.1,h_pad=0.1)

# Add legend
ax1.legend(
    prop={'size': 4},
    ncol=2,
    bbox_to_anchor=(1.0, 1.05),
    loc="lower right",
    bbox_transform=fig.transFigure)

# Add title
fig.text(
0.01,1.1,
'Examples of observed\nstorm regimes',
horizontalalignment='left',
verticalalignment='bottom',
size=8)

# Adjust width of border
for axis in ['top','bottom','left','right']:
    ax1.spines[axis].set_linewidth(0.7)
    ax2.spines[axis].set_linewidth(0.7)
    ax3.spines[axis].set_linewidth(0.7)


fig.savefig('12_c&p_observed_storm_impacts.png',dpi=600, bbox_inches = "tight")
plt.show()

# Swash zone volume change histogram
How much does the beach width change variation can we expect in the swash regime?

In [ ]:
impacts['observed'][impacts['observed'].storm_regime=='swash'].width_msl_change_pct.sort_values(ascending=False)

In [ ]:
import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(6, 3), dpi=300)
gs = gridspec.GridSpec(2, 3)
ax1 = fig.add_subplot(gs[0:2, 0:2])
ax2 = fig.add_subplot(gs[0, 2])
ax3 = fig.add_subplot(gs[1, 2], sharex=ax2)

# Histogram
ax1.hist(
    impacts['observed'][impacts['observed'].storm_regime=='swash'].width_msl_change_pct 
)

# Format axes, ticks and labels
ax1.set_xlabel('$\Delta$ beach width', size=8)
ax1.set_ylabel('Count', size=8)
ax1.xaxis.set_major_locator(ticker.MultipleLocator(25))
ax1.xaxis.set_major_formatter(ticker.PercentFormatter())
ax1.tick_params(axis='both', which='major', labelsize=7)

# Show erosion and accretion regions
ax1.autoscale(False)
ax1.fill([-100,0,0,-100], [0,0,500,500], '#f46d43', alpha=0.2,zorder=0)
ax1.fill([100,0,0,100], [0,0,500,500], '#abdda4', alpha=0.2,zorder=0)

ax1.text(
    0.95,
    0.95,
    'Accretion',
    transform=ax1.transAxes,
    size=8,
    horizontalalignment='right',
    verticalalignment='top',
    zorder=3,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

ax1.text(
    0.05,
    0.95,
    'Erosion',
    transform=ax1.transAxes,
    size=8,
    horizontalalignment='left',
    verticalalignment='top',
    zorder=3,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

# Add subplot letters
ax1.text(
    0.93,
    0.05,
    '(a)',
    transform=ax1.transAxes,
    size=10,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

# Profile subplots
prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'

plots = [
    {
        'ax': ax2,
        'title': '$\Delta$ beach width = $+83\%$',
        'site_id': 'MANNING0125',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': '(b)',
        'xlim_left' : 50,
    },
    {
        'ax': ax3,
        'title': '$\Delta$ beach width = $-73\%$',
        'site_id': 'DIAMONDn0024',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': '(c)',
        'xlim_left' : 100,
    },
]

for plot in plots:
    
    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])
    
    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--')
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color)
    
    if ax == ax2:
        z_pre = df_pro_pre.z.values
        z_pre[np.isnan(z_pre)] = 0
        
        # Only want to fill the difference between pre/post past a certain x-val
        mask = df_pro_pre.index.get_level_values('x') > plot['x_min_fill']
    
        ax.fill_between(
            df_pro_post.index.get_level_values('x')[mask],
            df_pro_post.z.values[mask],
            z_pre[mask],
            color='#abdda4',
            label='Accreted volume',
            alpha=0.4)
        
    
    if ax == ax3:
        # Fill to zero elevation if there is no post profile value
        z_post = df_pro_post.z.values
        z_post[np.isnan(z_post)] = 0

        # Only want to fill the difference between pre/post past a certain x-val
        mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

        ax.fill_between(
            df_pro_post.index.get_level_values('x')[mask],
            df_pro_pre.z.values[mask],
            z_post[mask],
            color='#f46d43',
            label='Eroded volume',
            alpha=0.4)
        
        # Add dummy legend entry
        ax.fill_between(
            [0,1],
            [0,0],
            [0,0],
            color='#abdda4',
            label='Accreted volume',
            alpha=0.4)
    
    # Set lims
    ax.set_ylim([0, 12])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    
    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=7)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=8)
    
    # Add subplot letters
    ax.text(
        0.04,
        0.08,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=10,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))
    
# Remove tick parameters from shared axis
ax2.tick_params(labelbottom=False)

# Axis labels
ax3.set_xlabel('Cross-shore position (m)', size=8)

# Change y-axis to right hand side
ax2.yaxis.tick_right()
ax3.yaxis.tick_right()


# Add common x-label
fig.text(
    0.98,
    0.5,
    'Elevation (mAHD)',
    ha='center',
    size=8,
    horizontalalignment='center',
    verticalalignment='center',
    rotation=90)

# Needs to be called before legend
fig.tight_layout()

# Add legend
ax3.legend(
    prop={'size': 6},
    ncol=2,
    bbox_to_anchor=(1.0, 0.97),
    loc="lower right",
    bbox_transform=fig.transFigure
)

# Add title
fig.text(
0.06,1.00,
'Variation in volume change for swash regime profiles',
horizontalalignment='left',
verticalalignment='bottom',
size=10)

fig.savefig('12_var_vol_change_swash_regime.png',dpi=300, bbox_inches = "tight")

In [ ]:
# For Coasts and Ports

import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(3, 1.5), dpi=300)
gs = gridspec.GridSpec(2, 3)
ax1 = fig.add_subplot(gs[0:2, 0:2])
ax2 = fig.add_subplot(gs[0, 2])
ax3 = fig.add_subplot(gs[1, 2], sharex=ax2)

# Histogram
ax1.hist(
    impacts['observed'][impacts['observed'].storm_regime ==
                        'swash'].width_msl_change_pct
)

# Format axes, ticks and labels
ax1.set_xlabel('$\Delta$ beach width', size=6)
ax1.set_ylabel('Count', size=6)
ax1.xaxis.set_major_locator(ticker.MultipleLocator(50))
ax1.xaxis.set_major_formatter(ticker.PercentFormatter())
ax1.tick_params(axis='both', which='major', labelsize=6)

# Show erosion and accretion regions
ax1.autoscale(False)
ax1.fill([-100, 0, 0, -100], [0, 0, 500, 500], '#f46d43', alpha=0.2, zorder=0)
ax1.fill([100, 0, 0, 100], [0, 0, 500, 500], '#abdda4', alpha=0.2, zorder=0)

ax1.text(
    0.95,
    0.95,
    'Accretion',
    transform=ax1.transAxes,
    size=6,
    horizontalalignment='right',
    verticalalignment='top',
    zorder=3,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

ax1.text(
    0.05,
    0.95,
    'Erosion',
    transform=ax1.transAxes,
    size=6,
    horizontalalignment='left',
    verticalalignment='top',
    zorder=3,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

# Add subplot letters
ax1.text(
    0.90,
    0.04,
    '(a)',
    transform=ax1.transAxes,
    size=8,
    bbox=dict(
        facecolor='white',
        alpha=0.0,
        edgecolor='white',
        boxstyle='square,pad=0'))

# Profile subplots
prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'

plots = [
    {
        'ax': ax2,
        'title': '$\Delta$ beach width = $+83\%$',
        'site_id': 'MANNING0125',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': '(b)',
        'xlim_left': 50,
    },
    {
        'ax': ax3,
        'title': '$\Delta$ beach width = $-73\%$',
        'site_id': 'DIAMONDn0024',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': '(c)',
        'xlim_left': 100,
    },
]

for plot in plots:

    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])

    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--',
        lw=1)
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color,
        lw=1)

    if ax == ax2:
        z_pre = df_pro_pre.z.values
        z_pre[np.isnan(z_pre)] = 0

        # Only want to fill the difference between pre/post past a certain x-val
        mask = df_pro_pre.index.get_level_values('x') > plot['x_min_fill']

        ax.fill_between(
            df_pro_post.index.get_level_values('x')[mask],
            df_pro_post.z.values[mask],
            z_pre[mask],
            color='#abdda4',
            label='Accreted volume',
            alpha=0.4)

    if ax == ax3:
        # Fill to zero elevation if there is no post profile value
        z_post = df_pro_post.z.values
        z_post[np.isnan(z_post)] = 0

        # Only want to fill the difference between pre/post past a certain x-val
        mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

        ax.fill_between(
            df_pro_post.index.get_level_values('x')[mask],
            df_pro_pre.z.values[mask],
            z_post[mask],
            color='#f46d43',
            label='Eroded volume',
            alpha=0.4)

        # Add dummy legend entry
        ax.fill_between(
            [0, 1],
            [0, 0],
            [0, 0],
            color='#abdda4',
            label='Accreted volume',
            alpha=0.4)

    # Set lims
    ax.set_ylim([0, 12])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(5))

    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=6)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=5)

    # Add subplot letters
    ax.text(
        0.04,
        0.15,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=8,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))


# Remove tick parameters from shared axis
ax2.tick_params(labelbottom=False)

# Remove tick lines but keep labels
ax2.tick_params(axis='y', which='both', length=0)
ax3.tick_params(axis='y', which='both', length=0)

# Axis labels
ax3.set_xlabel('Cross-shore position (m)', size=6)

# Change y-axis to right hand side
ax2.yaxis.tick_right()
ax3.yaxis.tick_right()

# Pad tick parameter labels
ax1.xaxis.set_tick_params(pad=-3)
ax2.xaxis.set_tick_params(pad=-3)
ax3.xaxis.set_tick_params(pad=-3)


# Add common x-label
fig.text(
    1.75,
    0.5,
    'Elevation (mAHD)',
    size=6,
    horizontalalignment='center',
    verticalalignment='center',
    rotation=90,
    transform=ax1.transAxes)

# Needs to be called before legend
fig.tight_layout(pad=0.5, h_pad=0.1, w_pad=0.2)

# Add legend
ax3.legend(
    prop={'size': 4.5},
    ncol=2,
    bbox_to_anchor=(1.0, 0.97),
    loc="lower right",
    bbox_transform=fig.transFigure
)

# Add title
fig.text(
    0.06, 1.14,
    'Variation in beach width\nchange for swash regime\nprofiles',
    horizontalalignment='left',
    verticalalignment='top',
    size=8)

# Adjust width of border
for axis in ['top', 'bottom', 'left', 'right']:
    ax1.spines[axis].set_linewidth(0.7)
    ax2.spines[axis].set_linewidth(0.7)
    ax3.spines[axis].set_linewidth(0.7)
    ax2.yaxis.set_tick_params(width=0.7)
    ax3.yaxis.set_tick_params(width=0.7)

fig.savefig('12_c&p_var_vol_change_swash_regime.png',
            dpi=600, bbox_inches="tight", pad_inches=0.01)
# fig.savefig('12_c&p_var_vol_change_swash_regime.svg',bbox_inches = "tight")

# Narrabeen section plots

In [ ]:
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(3, 5), dpi=150)
gs = gridspec.GridSpec(3, 1)
ax1 = fig.add_subplot(gs[0, 0])
ax2 = fig.add_subplot(gs[1, 0], sharex=ax1)
ax3 = fig.add_subplot(gs[2, 0], sharex=ax1)

prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'

plots = [
    {
        'ax': ax1,
        'title': '$\Delta$ Dune Vol = \SI{-13}{\m^{3}\per\m}',
        'site_id': 'NARRA0005',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': '(a)',
        'xlim_left' : 150,
    },
    {
        'ax': ax2,
        'title': '$\Delta$ Dune Vol = \SI{-10}{\m^{3}\per\m}',
        'site_id': 'NARRA0026',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': '(b)',
        'xlim_left' : 150,
    },
    {
        'ax': ax3,
        'title': '$\Delta$ Dune Vol = \SI{-21}{\m^{3}\per\m}',
        'site_id': 'NARRA0028',
        'x_min_fill': 190,
        'location': 'Avoca Lagoon\nEntrance',
        'subplot_letter': '(c)',
        'xlim_left' : 150,
    },
]

for plot in plots:
    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])
    df_feat_pre = df_profile_features_crest_toes.xs(
        (site_id, 'prestorm'), level=['site_id', 'profile_type'])
    df_feat_post = df_profile_features_crest_toes.xs(
        (site_id, 'poststorm'), level=['site_id', 'profile_type'])

    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--')
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color)
#     ax.scatter(
#         df_feat_post.dune_crest_x,
#         df_feat_post.dune_crest_z,
#         label='Poststorm dune crest',
#         facecolor=poststorm_color,
#         edgecolor='black',
#         linewidth='0.75',
#         marker='v',
#         zorder=3)
#     ax.scatter(
#         df_feat_pre.dune_crest_x,
#         df_feat_pre.dune_crest_z,
#         label='Prestorm dune crest',
#         facecolor=prestorm_color,
#         edgecolor='black',
#         linewidth='0.75',
#         marker='v',
#         zorder=3)

#     if not np.isnan(df_feat_post.dune_toe_x.values[0]):
#         ax.scatter(
#             df_feat_post.dune_toe_x,
#             df_feat_post.dune_toe_z,
#             label='Poststorm dune toe',
#             facecolor=poststorm_color,
#             edgecolor='black',
#             linewidth='0.75',
#             marker='^',
#             zorder=3)

#     if not np.isnan(df_feat_pre.dune_toe_x.values[0]):
#         ax.scatter(
#             df_feat_pre.dune_toe_x,
#             df_feat_pre.dune_toe_z,
#             label='Prestorm dune toe',
#             facecolor=prestorm_color,
#             edgecolor='black',
#             linewidth='0.75',
#             marker='^',
#             zorder=3)

    # Fill to zero elevation if there is no post profile value
    z_post = df_pro_post.z.values
    z_post[np.isnan(z_post)] = 0

    # Only want to fill the difference between pre/post past a certain x-val
    mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

    ax.fill_between(
        df_pro_post.index.get_level_values('x')[mask],
        df_pro_pre.z.values[mask],
        z_post[mask],
        color='#f46d43',
        label='Eroded volume',
        alpha=0.4)

    # Set lims
    ax.set_ylim([0, 14])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    
    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=7)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=8)

    # Add subplot letters
    ax.text(
        0.02,
        0.05,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=10,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

#     # Add text showing location
#     ax.text(
#         0.95,
#         0.95,
#         plot['location'],
#         transform=ax.transAxes,
#         size=8,
#         horizontalalignment='right',
#         verticalalignment='top',
#         zorder=3,
#         bbox=dict(
#             facecolor='white',
#             alpha=0.9,
#             edgecolor='white',
#             boxstyle='square,pad=0'))

# Remove tick parameters from shared axis
ax1.tick_params(labelbottom=False)
ax2.tick_params(labelbottom=False)



plt.tight_layout()

# Add y-label
ax3.set_xlabel('Cross-shore position (m)', size=8)

# Add common x-label
fig.text(
    0.0,
    0.5,
    'Elevation (mAHD)',
    ha='center',
    size=8,
    rotation=90,
    horizontalalignment='center',
    verticalalignment='center')

# # Add legend
# ax1.legend(
#     prop={'size': 6},
#     ncol=4,
#     bbox_to_anchor=(0.90, 1.0),
#     loc="lower right",
#     bbox_transform=fig.transFigure)

# # Add title
# fig.text(
# 0.06,1.01,
# 'Examples of observed\nstorm regimes',
# horizontalalignment='left',
# verticalalignment='bottom',
# size=10)


fig.savefig('12_narrabeen_triple_plot.png',dpi=300, bbox_inches = "tight")
plt.show()

In [ ]:
## For coasts and ports

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import matplotlib.ticker as ticker

# Setup grid
fig = plt.figure(figsize=(1, 1.5), dpi=150)
gs = gridspec.GridSpec(3, 1)
ax1 = fig.add_subplot(gs[0, 0])
ax2 = fig.add_subplot(gs[1, 0], sharex=ax1)
ax3 = fig.add_subplot(gs[2, 0], sharex=ax1)

prestorm_color = '#fdae61'
poststorm_color = '#d53e4f'

plots = [
    {
        'ax': ax1,
        'title': '$\Delta$ Dune Vol = \SI{-13}{\m^{3}\per\m}',
        'site_id': 'NARRA0005',
        'x_min_fill': 150,
        'location': 'Grants\nBeach',
        'subplot_letter': 'Profile A',
        'xlim_left': 150,
    },
    {
        'ax': ax2,
        'title': '$\Delta$ Dune Vol = \SI{-10}{\m^{3}\per\m}',
        'site_id': 'NARRA0026',
        'x_min_fill': 150,
        'location': 'Manning\nPoint',
        'subplot_letter': 'Profile B',
        'xlim_left': 150,
    },
    {
        'ax': ax3,
        'title': '$\Delta$ Dune Vol = \SI{-21}{\m^{3}\per\m}',
        'site_id': 'NARRA0028',
        'x_min_fill': 190,
        'location': 'Avoca Lagoon\nEntrance',
        'subplot_letter': 'Profile C',
        'xlim_left': 150,
    },
]

for plot in plots:
    ax = plot['ax']
    site_id = plot['site_id']
    df_pro_pre = df_profiles.xs((site_id, 'prestorm'),
                                level=['site_id', 'profile_type'])
    df_pro_post = df_profiles.xs((site_id, 'poststorm'),
                                 level=['site_id', 'profile_type'])
    df_feat_pre = df_profile_features_crest_toes.xs(
        (site_id, 'prestorm'), level=['site_id', 'profile_type'])
    df_feat_post = df_profile_features_crest_toes.xs(
        (site_id, 'poststorm'), level=['site_id', 'profile_type'])

    ax.plot(
        df_pro_post.index.get_level_values('x'),
        df_pro_post.z.values,
        label='Poststorm profile',
        color=poststorm_color,
        linestyle='--')
    ax.plot(
        df_pro_pre.index.get_level_values('x'),
        df_pro_pre.z.values,
        label='Prestorm profile',
        color=prestorm_color)
    #     ax.scatter(
    #         df_feat_post.dune_crest_x,
    #         df_feat_post.dune_crest_z,
    #         label='Poststorm dune crest',
    #         facecolor=poststorm_color,
    #         edgecolor='black',
    #         linewidth='0.75',
    #         marker='v',
    #         zorder=3)
    #     ax.scatter(
    #         df_feat_pre.dune_crest_x,
    #         df_feat_pre.dune_crest_z,
    #         label='Prestorm dune crest',
    #         facecolor=prestorm_color,
    #         edgecolor='black',
    #         linewidth='0.75',
    #         marker='v',
    #         zorder=3)

    #     if not np.isnan(df_feat_post.dune_toe_x.values[0]):
    #         ax.scatter(
    #             df_feat_post.dune_toe_x,
    #             df_feat_post.dune_toe_z,
    #             label='Poststorm dune toe',
    #             facecolor=poststorm_color,
    #             edgecolor='black',
    #             linewidth='0.75',
    #             marker='^',
    #             zorder=3)

    #     if not np.isnan(df_feat_pre.dune_toe_x.values[0]):
    #         ax.scatter(
    #             df_feat_pre.dune_toe_x,
    #             df_feat_pre.dune_toe_z,
    #             label='Prestorm dune toe',
    #             facecolor=prestorm_color,
    #             edgecolor='black',
    #             linewidth='0.75',
    #             marker='^',
    #             zorder=3)

    # Fill to zero elevation if there is no post profile value
    z_post = df_pro_post.z.values
    z_post[np.isnan(z_post)] = 0

    # Only want to fill the difference between pre/post past a certain x-val
    mask = df_pro_post.index.get_level_values('x') > plot['x_min_fill']

    ax.fill_between(
        df_pro_post.index.get_level_values('x')[mask],
        df_pro_pre.z.values[mask],
        z_post[mask],
        color='#f46d43',
        label='Eroded volume',
        alpha=0.4)

    # Set lims
    ax.set_ylim([0, 14])
    ax.set_xlim(left=plot['xlim_left'])

    # Set ticks to 50 m
    ax.xaxis.set_major_locator(ticker.MultipleLocator(50))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(5))
    ax.yaxis.set_tick_params(pad=-3)
    ax.xaxis.set_tick_params(pad=-3)

    # Change tick label size
    ax.tick_params(axis='both', which='major', labelsize=6)

    # Add titles showing regimes
    ax.set_title(plot['title'], size=6)

    # Add subplot letters
    ax.text(
        0.60,
        0.6,
        plot['subplot_letter'],
        transform=ax.transAxes,
        size=6,
        bbox=dict(
            facecolor='white',
            alpha=0.9,
            edgecolor='white',
            boxstyle='square,pad=0'))

#     # Add text showing location
#     ax.text(
#         0.95,
#         0.95,
#         plot['location'],
#         transform=ax.transAxes,
#         size=8,
#         horizontalalignment='right',
#         verticalalignment='top',
#         zorder=3,
#         bbox=dict(
#             facecolor='white',
#             alpha=0.9,
#             edgecolor='white',
#             boxstyle='square,pad=0'))

# Remove tick parameters from shared axis
ax1.tick_params(labelbottom=False)
ax2.tick_params(labelbottom=False)

plt.tight_layout(pad=0.1, w_pad=0.1, h_pad=0.1)

# Add x-label
ax3.set_xlabel('Cross-shore position (m)', size=6)

# Add common y-label
fig.text(
    -0.05,
    0.5,
    'Elevation (mAHD)',
    ha='center',
    size=6,
    rotation=90,
    horizontalalignment='center',
    verticalalignment='center')

# # Add legend
# ax1.legend(
#     prop={'size': 6},
#     ncol=4,
#     bbox_to_anchor=(0.90, 1.0),
#     loc="lower right",
#     bbox_transform=fig.transFigure)

# # Add title
# fig.text(
# 0.06,1.01,
# 'Examples of observed\nstorm regimes',
# horizontalalignment='left',
# verticalalignment='bottom',
# size=10)

# Adjust width of border
for axis in ['top', 'bottom', 'left', 'right']:
    ax1.spines[axis].set_linewidth(0.7)
    ax2.spines[axis].set_linewidth(0.7)
    ax3.spines[axis].set_linewidth(0.7)

fig.savefig(
    '12_c&p_narrabeen_triple_plot.png',
    dpi=600,
    bbox_inches="tight",
    pad_inches=0.01)
plt.show()

In [ ]:
df_sites.groupby('beach').mean()[['lat','lon']].to_dict('index')